# Capital Flow Model

In [1]:
import tushare as ts
import pandas as pd

In [2]:
pro = ts.pro_api('68bbfd78066631454037489152fda2734d169b219347228eb8866135')#please input you tushare account in the branket 

In [3]:
#Select stocks to be traded on the Shanghai Stock Exchange
data = pro.stock_basic(exchange='', list_status='L', fields='ts_code,symbol,name,exchange,industry,list_date')
data=data[data['exchange'].str.contains('SSE')]

In [4]:
# Shares issued after the test start date ('2013-01-01')
date=['2021','2020','2019','2018','2017','2016','2015','2014','2013']
num=0
for x in date:
    num=data[data['list_date'].str.contains(x)]['ts_code'].count()+num

In [5]:
data=data.sort_values(by='list_date', ascending=False).iloc[num:]
data.reset_index(inplace=True)
del data['index']
data

ts_code  symbol   name industry exchange list_date
0    603003.SH  603003   龙宇燃油     石油贸易      SSE  20120817
1    603766.SH  603766   隆鑫通用      摩托车      SSE  20120810
2    601038.SH  601038   一拖股份     农用机械      SSE  20120808
3    603077.SH  603077   和邦生物     化工原料      SSE  20120731
4    603008.SH  603008    喜临门     家居用品      SSE  20120717
..         ...     ...    ...      ...      ...       ...
908  600602.SH  600602   云赛智联     软件服务      SSE  19901219
909  600601.SH  600601   ST方科     IT设备      SSE  19901219
910  600653.SH  600653   申华控股     汽车服务      SSE  19901219
911  600651.SH  600651   飞乐音响     电器仪表      SSE  19901219
912  600652.SH  600652  *ST游久      互联网      SSE  19901219

[913 rows x 6 columns]

In [6]:
stock_code=data['ts_code']# test stocks' code
stock_code

0      603003.SH
1      603766.SH
2      601038.SH
3      603077.SH
4      603008.SH
         ...    
908    600602.SH
909    600601.SH
910    600653.SH
911    600651.SH
912    600652.SH
Name: ts_code, Length: 913, dtype: object

In [30]:
stocks = pd.DataFrame()
count = 0
stock_code=data['ts_code']
dic = {}
for l in stock_code:
    #get each stocks' daily net money flow volumn and net money flow amount during the test date
    df1 = pro.moneyflow(ts_code=l, start_date='20130101',end_date='20151231',fields='ts_code,trade_date,net_mf_vol,net_mf_amount')
    #get each stocks' daily Capital stock outstanding (10,000 shares)
    df2= pro.query('daily_basic', ts_code=l, start_date='20130101', end_date='20151231',fields='ts_code,trade_date,float_share')
    # get each stocks' daily close price and  previous day close price
    df3= pro.daily(ts_code=l, start_date='20130101', end_date='20151231',fields='ts_code,trade_date,close,pre_close')
    
    df1 = df1.iloc[::-1]
    df2 = df2.iloc[::-1]
    df3 = df3.iloc[::-1]
    
    # get relevant flow for each stocks
    relevant_flow = df1['net_mf_amount'] / df1['net_mf_vol']
    
    #Take the 30-day period moving average of the relative capital flow
    relevant_flow = relevant_flow.rolling(30).mean().loc[::30]
    
    # previous day stoks's circulating market value 
    l1 = df1.shift(1)['net_mf_amount'] * df2.shift(1)['float_share'] - df1['net_mf_amount'] * df2['float_share']
    # stoks's circulating market value
    l2 = df1.shift(1)['net_mf_amount'] - df1['net_mf_amount']
    leverage = l1 / l2
    #Take the 30-day period moving average of the capital leverage
    leverage = leverage.rolling(30).mean().loc[::30]
    
    # get the mean of 5 days net money flow percentage changes which represent as capital momentum 
    #and then take the 30-day period moving average of the capital momentum 
    kinetic_energy = df1.rolling(5)['net_mf_amount'].mean().pct_change(5).rolling(30).mean().loc[::30]
    
    #get stocks' daily returns
    returns = df3['close'] / df3['pre_close'] - 1
    #Take the 30-day period moving average of the rate of return
    returns = returns.rolling(30).mean().loc[::30]
    
    dic[l] = pd.concat([returns, relevant_flow , leverage, kinetic_energy], keys=['return','relevant_flow','leverage','kinetic_energy'], axis=1)

In [31]:
# key represent date ,to avoid conflicts about different stocks available date
dictionary = {} 
for l in stock_code:
    for i in dic[l].index:
        dictionary[i] = dictionary.setdefault(i,[]) + [(l, dic[l].loc[i])]

In [32]:
for i in dictionary.keys():
    for j in range(len(dictionary[i])):
        dictionary[i][j][1].fillna(0, inplace=True)

In [18]:
dictionary

{642: [('603003.SH',
   return            0.0
   relevant_flow     4.0
   leverage          4.0
   kinetic_energy    8.0
   Name: 642, dtype: float64),
  ('601899.SH',
   return            -0.002501
   relevant_flow      5.000000
   leverage          15.000000
   kinetic_energy    14.000000
   Name: 642, dtype: float64),
  ('600984.SH',
   return            0.0
   relevant_flow     3.0
   leverage          3.0
   kinetic_energy    7.0
   Name: 642, dtype: float64),
  ('600579.SH',
   return            -0.000594
   relevant_flow     11.000000
   leverage           6.000000
   kinetic_energy     3.000000
   Name: 642, dtype: float64),
  ('600531.SH',
   return            -0.003179
   relevant_flow     15.000000
   leverage           7.000000
   kinetic_energy     1.000000
   Name: 642, dtype: float64),
  ('600037.SH',
   return            -0.001668
   relevant_flow     14.000000
   leverage          14.000000
   kinetic_energy     0.000000
   Name: 642, dtype: float64),
  ('600255.SH',
 

In [27]:
#test model of return with only relevant_flow as factor
rele_flow_return = 0
rele_flow = []
for i in dictionary.keys():
    rele_flow = [s[1][['return','relevant_flow']] for s in dictionary[i]]
    rele_flow.sort(key=lambda k:k['relevant_flow'], reverse=True)
    rele_flow = rele_flow[:30]
    for k in rele_flow:
        rele_flow_return += k[0]
rele_flow_return

36.474625833354914

In [12]:
#test model of return with only leverage as factor
leverage_return = 0
lever = []
for i in dictionary.keys():
    lever = [s[1][['return','leverage']] for s in dictionary[i]]
    lever.sort(key=lambda k:k['leverage'], reverse=True)
    lever = lever[:30]
    for k in lever:
        leverage_return += k[0]
leverage_return

26.610130669479386

In [13]:
#test model of return with only kinetic as factor
kinetic_return = 0
energy = []
for i in dictionary.keys():
    energy = [s[1][['return','kinetic_energy']] for s in dictionary[i]]
    energy.sort(key=lambda k:k['kinetic_energy'], reverse=True)
    energy = energy[:30]
    for k in energy:
        kinetic_return += k[0]
kinetic_return

25.731401484543355

Because the scores may be the same, the rate of return calculated with the following code has two cases. Although the results of the two runs are different, there is no problem with the rate of return, just because the top 30 stocks are not necessarily the same, so the results are different.


In [37]:
#Test the composite model
flow_lever = 0 # record renturn on Relative Fund Flow and Fund Leverage
flow_lever_arr = []
flow_kin = 0 # record renturn on Relative Fund Flow and Capital momentum 
flow_kin_arr = []
lever_kin = 0 # record renturn on Capital leverage and Capital momentum 
lever_kin_arr = []
flow_lever_kin= 0 # record renturn on Relative Fund Flow, Capital Leverage and Capital momentum
flow_lever_kin_arr = []
dicc = []
for i in dictionary.keys():
    dicc = [s[1] for s in dictionary[i]]
    dicc.sort(key=lambda k: k['relevant_flow'], reverse=True)
    for j, d in enumerate(dicc):
        d['relevant_flow'] = j
    dicc.sort(key=lambda k: k['leverage'], reverse=True)
    for j, d in enumerate(dicc):
        d['leverage'] = j
    dicc.sort(key=lambda k: k['kinetic_energy'], reverse=True)
    for j, d in enumerate(dicc):
        d['kinetic_energy'] = j
  
    # test model of return with relevant_flow and leverage as factors 
    for di in dicc:
        flow_lever_arr.append((di['return'], di['relevant_flow']+di['leverage']))
    flow_lever_arr.sort(key=lambda k: k[1])
    for k in flow_lever_arr[:30]:
        flow_lever += k[0]
    
    # test model of return with relevant_flow and kinetic_energy as factors
    for di in dicc:
        flow_kin_arr.append((di['return'], di['relevant_flow']+di['kinetic_energy']))
    flow_kin_arr.sort(key=lambda k: k[1])
    for k in flow_kin_arr[:30]:
        flow_kin += k[0]
    
    # test model of return with leverage and kinetic as factors
    for di in dicc:
        lever_kin_arr.append((di['return'], di['leverage']+di['kinetic_energy']))
    lever_kin_arr.sort(key=lambda k: k[1])
    for k in lever_kin_arr[:30]:
        lever_kin += k[0]
    
    # test model of return with mflow, leverage and kinetic as factor
    for di in dicc:
        flow_lever_kin_arr.append((di['return'], di['relevant_flow']+di['kinetic_energy']+di['leverage']))
    flow_lever_kin_arr.sort(key=lambda k: k[1])
    for k in flow_lever_kin_arr[:30]:
        flow_lever_kin += k[0]
    
print("flow_lever: ", flow_lever) 
print("flow_kin: ", flow_kin)
print("lever_kin: ", lever_kin)
print("flow_lever_kin: ", flow_lever_kin)

flow_lever:  48.72246991350963
flow_kin:  8.571998969140916
lever_kin:  44.648059336985845
flow_lever_kin:  48.258672328123666


In [17]:
# using the best model (Relative capital flow and Capital momentum ) summary all the stocks in target
flow_kin_arr = []
target = {}
for i in dictionary.keys():
    target[i] = []
    dicc = [s[:2] for s in dictionary[i]]
    dicc.sort(key=lambda k: k[1]['relevant_flow'], reverse=True)
    for j, d in enumerate(dicc):
        d[1]['relevant_flow'] = j
    dicc.sort(key=lambda k: k[1]['kinetic_energy'], reverse=True)
    for j, d in enumerate(dicc):
        d[1]['kinetic_energy'] = j
        
    for di in dicc:
        flow_kin_arr.append((di[0], di[1]['relevant_flow']+di[1]['kinetic_energy']))
    flow_kin_arr.sort(key=lambda k: k[1])
    for k in flow_kin_arr[:30]:
        target[i].append(k[0])
#target is our selection for stocks in each routine
target

{642: ['600623.SH',
  '600715.SH',
  '600109.SH',
  '600255.SH',
  '600984.SH',
  '603003.SH',
  '600037.SH',
  '600579.SH',
  '600531.SH',
  '600127.SH',
  '600162.SH',
  '601899.SH',
  '600117.SH',
  '600784.SH',
  '600172.SH',
  '600843.SH'],
 612: ['600623.SH',
  '600715.SH',
  '600623.SH',
  '600109.SH',
  '601899.SH',
  '600710.SH',
  '600255.SH',
  '600984.SH',
  '600758.SH',
  '603003.SH',
  '600117.SH',
  '600109.SH',
  '600037.SH',
  '600579.SH',
  '600843.SH',
  '600255.SH',
  '600157.SH',
  '600531.SH',
  '600172.SH',
  '600162.SH',
  '601388.SH',
  '600127.SH',
  '600784.SH',
  '600162.SH',
  '601899.SH',
  '600117.SH',
  '600784.SH',
  '600172.SH',
  '600843.SH',
  '600984.SH'],
 582: ['600623.SH',
  '600715.SH',
  '600623.SH',
  '600109.SH',
  '601899.SH',
  '600710.SH',
  '600255.SH',
  '600117.SH',
  '600623.SH',
  '600255.SH',
  '600984.SH',
  '600758.SH',
  '600862.SH',
  '603003.SH',
  '600843.SH',
  '600117.SH',
  '600109.SH',
  '600109.SH',
  '600037.SH',
  '60057

# Asymmetric Bollinger Bands Model

### rice quant back testing code

In [ ]:
%%rqalpha -s start -e end -p -bm 000001.XSHG  --account stock 100000

import talib

def init(context):
    context.stocks = target
    context.ma = 30
    context.boll = 90
    context.bolu = 50
    context.bold = 20
    context.signal = [0] * 30
    logger.info("RunInfo: {}".format(context.run_info))

def handle_bar(context, bar_dict):
    for i, s in enumerate(context.stocks):
        prices = history_bars(s, context.boll+2, '1d', 'close')
    
        MA = talib.SMA(prices, context.ma)
        BOLL = talib.SMA(prices, context.boll)
        BOLU = talib.SMA(prices, context.bolu) + 2 * talib.STDDEV(prices, context.bolu, 1)
        BOLD = talib.SMA(prices, context.bold) - 2 * talib.STDDEV(prices, context.bold, 1)
        BB = (prices - BOLD) / (BOLU - BOLD)
        BB_pct = talib.SMA(BB, 3)
        WIDTH = (BOLU - BOLD) / BOLL
        BIAS = (prices - MA) / MA
        WIDUP, WIDMA, WIDDN = talib.BBANDS(WIDTH, len(WIDTH), 2)
        
        # price position jdgement
        if BB[-1] >= 1 and BB_pct[-1] <= 0:
            order_target_percent(s, 0.2)
        elif BB[-1] <= 0 and BB_pct[-1] > 0:
            order_shares(s, 1000)
        
        # width judgement
        elif WIDTH[-1] < WIDDN[-1]:
            if BB[-1] >= 1 and MA[-1] < 0:
                order_shares(s, -1000)
            elif BB[-1] <= 0 and MA[-1] > 0:
                order_shares(s, 1000)
        elif WIDTH[-1] > WIDUP[-1]:
            if BB[-1] >= 1 and MA[-1] > 0:
                order_shares(s, 1000)
            elif BB[-1] <= 0 and MA[-1] < 0:
                order_shares(s, -1000)
        
        # bias judgement
        elif BIAS[-1] > 0.16:
            order_shares(s, -1000)
        elif BIAS[-1] < -0.16:
            order_shares(s, 1000)
        
        # bands judgement
        else:
            if BOLL[-1] > BOLL[-2]:
                if BB[-1] >= 1:
                    context.signal[i] = -1
                    if MA[-1] > MA[-2]:
                        order_shares(s, 1000)
                    elif MA[-1] < MA[-2]:
                        order_target_percent(s, 0.2)  
                elif BB[-1] <= 0:
                    if MA[-1] > MA[-2]:
                        context.signal[i] = 0
                        order_shares(s, 1000)
                    elif MA[-1] < MA[-2]:
                        if context.signal[i] == -1:
                            order_shares(s, -1000)
                        else:
                            context.signal[i] = 0
                            order_shares(s, 1000)
                else:
                    
                    if MA[-1] > MA[-2]:
                        context.signal[i] = 0
                        order_shares(s, 1000)
                    elif MA[-1] < MA[-2]:
                        if context.signal[i] == -1:
                            order_shares(s, -1000)
                        else:
                            context.signal[i] = 0
            else:
                if BB[-1] <= 0:
                    context.signal[i] = 1
                    if MA[-1] > MA[-2]:
                        order_shares(s, 1000)
                    elif MA[-1] < MA[-2]:
                        order_shares(s, -1000)
                elif BB[-1] >= 1:
                    if MA[-1] < MA[-2]:
                        context.signal[i] = 0
                        order_target_percent(s, 0.2)
                    elif MA[-1] > MA[-2]:
                        if context.signal[i] == 1:
                            order_shares(s, 1000)
                        else:
                            context.signal[i] = 0
                            order_shares(s, -1000)
                else:
                    if MA[-1] < MA[-2]:
                        context.signal[i] = 0
                        order_shares(s, -1000)
                    elif MA[-1] > MA[-2]:
                        if context.signal[i] == 1:
                            order_shares(s, 1000)
                        else:
                            context.signal[i] = 0